# Python with PostgreSQL & PostGIS

<span style="color: blue;">Note: Please always run the complete Jupyter Notebook from the beginning, as object names such as 'sql' and 'gdf' are reused in the code cells.</span>

## Libraries and Settings

In [1]:
# Libraries
import os
import folium
import pandas as pd
import geopandas as gpd
from sqlalchemy import create_engine, text

# Ignore warnings
import warnings
warnings.filterwarnings("ignore")

print(os.getcwd())

/workspaces/python_postgresql_postgis


## Create database connection

In [2]:
# Set up database connection
user = "pgadmin"
password = "geheim"
host = "localhost"
port = "5432"
database = "osm_switzerland"

# Create Connection URL
db_connection_url = "postgresql://" + user + ":" + password +\
                    "@" + host + ":" + port + "/" + database

# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Test database connection
with engine.connect() as connection:
    result = connection.execute(text('SELECT current_database()'))
    print(result.fetchone())

# Dispose the engine
engine.dispose()

('osm_switzerland',)


## List tables in database

In diesem Codeabschnitt wird eine Verbindung zu einer PostgreSQL-Datenbank hergestellt, um die Namen der Tabellen im Schema 'public' (öffentliche Tabellen) abzufragen.

- Die Methode execute() führt eine SQL-Abfrage aus, die die Namen aller Tabellen im Schema 'public' der Datenbank abruft.
- information_schema.tables ist eine Systemtabelle in PostgreSQL, die Metadaten über die Tabellen in der Datenbank enthält.
- table_schema = 'public' filtert die Tabellen auf diejenigen, die im öffentlichen Schema liegen.

In [3]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Open a connection
with engine.connect() as connection:

    # Execute the query
    result = connection.execute(text("""SELECT table_name
                                        FROM information_schema.tables
                                        WHERE table_schema = 'public';"""))
    
    # Fetch and print the results
    for row in result:
        print(row[0])

# Dispose the engine
engine.dispose()

geography_columns
geometry_columns
spatial_ref_sys
planet_osm_polygon
planet_osm_point
planet_osm_line
planet_osm_roads


## Show columns and data types of selected table
Dieser Codeabschnitt stellt eine Verbindung zur PostgreSQL-Datenbank her, führt eine SQL-Abfrage aus, um die Spaltennamen und Datentypen der Tabelle planet_osm_polygon abzurufen, speichert diese Informationen in einem Pandas DataFrame und gibt sie schließlich aus.

In [4]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Specify your table name
table_name = 'planet_osm_polygon'

# Query to get column information
query = f"""SELECT column_name, data_type 
        FROM information_schema.columns 
        WHERE table_name = '{table_name}'"""

# Execute the query and read the result into a DataFrame
df = pd.read_sql(query, engine)

# Dispose the engine
engine.dispose()

# Print the DataFrame
df

column_name     data_type
0             osm_id        bigint
1            z_order       integer
2           way_area          real
3                way  USER-DEFINED
4   addr:housenumber          text
..               ...           ...
68              wood          text
69         tracktype          text
70            access          text
71    addr:housename          text
72       addr:street          text

[73 rows x 2 columns]

## Query: Select buildings for which full address is available in defined zip code areas

- SQLAlchemy-Engine erstellen: Es wird eine Verbindung zur PostgreSQL-Datenbank hergestellt.
- SQL-Abfrage definieren: Diese Abfrage wählt Gebäude aus der OSM-Tabelle planet_osm_polygon aus, für die die Adresse (Straße, Hausnummer, Stadt, Postleitzahl) vollständig definiert ist. Die Postleitzahlen müssen entweder 8001 oder 8002 sein (Bereiche in Zürich). Zusätzlich wird die Geometrie der Gebäude in das Koordinatensystem EPSG:4326 transformiert (dieses System wird häufig für Karten verwendet, z.B. in Webanwendungen).
- Abfrage ausführen und Ergebnisse speichern: Die Abfrage wird in ein GeoDataFrame geladen, das sowohl die räumlichen Daten (Geometrie der Gebäude) als auch die Attributdaten (Adresse) speichert.
- Verbindung schließen: Die Verbindung zur Datenbank wird geschlossen.
- GeoDataFrame anzeigen: Das Ergebnis der Abfrage wird ausgegeben.

Dieses GeoDataFrame enthält also die Gebäude in Zürich (Postleitzahlen 8001, 8002) mit vollständiger Adresse und der dazugehörigen Geometrie.

In [5]:
## Abfrage: Wähle Gebäude aus, für die eine vollständige Adresse in definierten Postleitzahlenbereichen verfügbar ist

# Erstelle eine SQLAlchemy-Engine zur Verbindung mit der PostgreSQL-Datenbank
engine = create_engine(db_connection_url)

# Define SQL query 
sql = """SELECT
                p.osm_id,                  -- OSM-ID des Objekts (eindeutiger Bezeichner)
                p."addr:street",            -- Straßenname des Gebäudes
                p."addr:housenumber",       -- Hausnummer des Gebäudes
                p."addr:city",              -- Stadt, in der sich das Gebäude befindet
                p."addr:postcode",          -- Postleitzahl des Gebäudes
                p.building,                 -- Typ des Gebäudes (z.B. Wohnhaus, Geschäftsgebäude)
                st_transform(p.way, 4326) AS geom -- Geometrie (Position des Gebäudes) im EPSG:4326-Koordinatensystem
        FROM
                public.planet_osm_polygon AS p  -- Auswahl aus der Tabelle planet_osm_polygon, die Polygone (Flächen) enthält
        WHERE
                p."addr:street" IS NOT NULL    -- Die Straße muss definiert sein
                AND p."addr:housenumber" IS NOT NULL -- Die Hausnummer muss definiert sein
                AND p."addr:city" IS NOT NULL  -- Die Stadt muss definiert sein
                AND p."addr:postcode" IN ('8001', '8002') -- Die Postleitzahl muss 8001 oder 8002 sein (in Zürich)"""

# Führe die SQL-Abfrage aus und speichere das Ergebnis in einem GeoDataFrame
# GeoDataFrame speichert räumliche Daten (Geometrien) zusammen mit Attributen
gdf = gpd.GeoDataFrame.from_postgis(sql, engine)

# Schließe die Engine, um die Verbindung zur Datenbank zu beenden
engine.dispose()

# Gib das GeoDataFrame aus, um das Ergebnis der Abfrage anzuzeigen
gdf


osm_id          addr:street addr:housenumber addr:city addr:postcode  \
0      24910306      Leonhardstrasse               18    Zürich          8001   
1     315044631      Leonhardstrasse               13    Zürich          8001   
2     315044630      Leonhardstrasse               11    Zürich          8001   
3     315044635      Leonhardstrasse                9    Zürich          8001   
4     501215139      Weinbergstrasse              42c    Zürich          8001   
...         ...                  ...              ...       ...           ...   
2350  108633058  Brandschenkestrasse              152    Zürich          8002   
2351  108633096  Brandschenkestrasse             152c    Zürich          8002   
2352  108633055  Brandschenkestrasse             152b    Zürich          8002   
2353  108626600  Brandschenkestrasse             110a    Zürich          8002   
2354   34572240  Brandschenkestrasse              110    Zürich          8002   

         building                                               geom  
0     residential  POLYGON ((8.54556 47.37762, 8.54561 47.37755, ...  
1      apartments  POLYGON ((8.54565 47.37863, 8.54574 47.37849, ...  
2      apartments  POLYGON ((8.54559 47.37872, 8.54565 47.37863, ...  
3      apartments  POLYGON ((8.54555 47.37878, 8.54559 47.37872, ...  
4            None  POLYGON ((8.54415 47.38017, 8.54417 47.3801, 8...  
...           ...                                                ...  
2350   industrial  POLYGON ((8.52413 47.36489, 8.52415 47.36477, ...  
2351       office  POLYGON ((8.52388 47.36409, 8.52391 47.3639, 8...  
2352   industrial  POLYGON ((8.5239 47.36435, 8.5239 47.36431, 8....  
2353       office  POLYGON ((8.52458 47.3655, 8.52462 47.36534, 8...  
2354   commercial  POLYGON ((8.52469 47.36579, 8.52476 47.36552, ...  

[2355 rows x 7 columns]

## Show selected features on map

<span style="color: blue;">Note the popup field in the map, which has been added to provide additional information about buildings.</span>

<span style="color: blue;">Example of alternative background maps (maptiles) are:</span>
- <span style="color: blue;">EsriWorldImagery</span>
- <span style="color: blue;">EsriWorldTopoMap</span>
- <span style="color: blue;">EsriWorldGrayCanvas</span>
- <span style="color: blue;">CartoDBDarkMatter</span>
- <span style="color: blue;">CartoDBPositron</span>


In [6]:
# Stellt sicher, dass das GeoDataFrame die richtige Projektion (Koordinatensystem) hat, nämlich EPSG:4326 (WGS84)
# EPSG:4326 ist das gebräuchliche Koordinatensystem für geografische Daten, das Längen- und Breitengrade verwendet.
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)  # Setzt das Koordinatensystem auf EPSG:4326, falls es nicht vorhanden ist
else:
    pass  # Falls die Projektion bereits vorhanden ist, wird nichts getan

# Berechne die Mittelpunkte (Centroid) der Geometrien (z.B. Gebäude), um den Mittelpunkt der Karte zu finden
centroids = gdf.geometry.centroid  # Berechnet den Mittelpunkt jedes Gebäudes (Polygone)
lon = centroids.x.mean()  # Berechnet den Durchschnitt der Längengrade (x-Koordinate), um den zentralen Längengrad zu ermitteln
lat = centroids.y.mean()  # Berechnet den Durchschnitt der Breitengrade (y-Koordinate), um den zentralen Breitengrad zu ermitteln

# Initialisiere die Karte mit dem berechneten zentralen Längen- und Breitengrad, damit die Karte das relevante Gebiet zeigt
# Der Parameter zoom_start bestimmt den anfänglichen Zoom-Level der Karte (15 ist eine relativ große Vergrößerung)
m = folium.Map(location=[lat, lon], 
               zoom_start=15,  # Startzoom für eine detaillierte Ansicht
               tiles='EsriWorldImagery')  # Verwendet den EsriWorldImagery-Kartenstil als Hintergrund (Satellitenbild)

# Füge die GeoJSON-Daten der Karte hinzu
# Dies stellt die geometrischen Daten (Gebäude) dar und ermöglicht die Visualisierung auf der Karte
folium.GeoJson(
    gdf,  # Das GeoDataFrame mit den geometrischen und Attributdaten
    name='geojson',  # Der Layer-Name, unter dem die Daten in der Karte erscheinen
    weight=0.5,  # Die Linienstärke für die Umrandung der Gebäude
    fill_color='greenyellow',  # Füllfarbe für die Gebäude (grün-gelb)
    fillOpacity=0.8,  # Die Transparenz der Füllfarbe (0.8 = leicht transparent)
    # Konfiguration des Popups, das angezeigt wird, wenn ein Benutzer auf ein Gebäude klickt
    popup=folium.GeoJsonPopup(fields=['addr:street',   # Zeigt den Straßennamen an
                                      'addr:housenumber',  # Zeigt die Hausnummer an
                                      'addr:city',  # Zeigt die Stadt an
                                      'addr:postcode',  # Zeigt die Postleitzahl an
                                      'building'])  # Zeigt den Gebäudetyp an (z.B. Wohngebäude, Geschäftsgebäude)
).add_to(m)  # Fügt diese Ebene zur Karte hinzu

# Fügt eine Steuerung zur Karte hinzu, um zwischen verschiedenen Ebenen zu wechseln (z.B. verschiedene Hintergrundkarten)
folium.LayerControl().add_to(m)

# Zeigt die Karte an (in Jupyter Notebooks wird die Karte direkt im Notebook angezeigt) => m

In [7]:
# legt den Mittelpunt der Karte fest (mit gesuchten Longitude/Latidude) damit es nciht irgendwohin psringt
# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Calculate the mean longitude and latitude for the map center
centroids = gdf.geometry.centroid
lon = centroids.x.mean()
lat = centroids.y.mean()

# Initialize the map (zoom_start => zoom-Faktor an Karte)
m = folium.Map(location=[lat, lon], 
               zoom_start=15,
               tiles='EsriWorldImagery')

# Map settings
folium.GeoJson(
    gdf,
    name='geojson',
    weight=0.5,
    fill_color='greenyellow',
    fillOpacity=0.8,
    popup=folium.GeoJsonPopup(fields=['addr:street',
                                      'addr:housenumber',
                                      'addr:city',
                                      'addr:postcode',
                                      'building'])
).add_to(m)

folium.LayerControl().add_to(m)

# Plot map
m

Um den Code anzupassen, um Gebäude in Bern (statt Zürich) mit vollständigen Adressen anzuzeigen, musst du hauptsächlich die Postleitzahlen in der SQL-Abfrage ändern, die Bern entsprechen. Hier sind einige typische Postleitzahlen von Bern:

- Bern Stadtzentrum: 3000, 3011, 3012, 3013

Die Gebäude, die auf der Karte grün markiert werden, werden aus der PostgreSQL-Datenbank (mit PostGIS-Erweiterung) gefiltert. Der Filter wird in der SQL-Abfrage definiert, die Teil des Codes ist. Konkret wird hier die Tabelle public.planet_osm_polygon verwendet, die Gebäudepolygone enthält.
Die Filterbedingungen für die Gebäude:

In der SQL-Abfrage werden Gebäude gefiltert, die:

    Eine vollständige Adresse haben (Straße, Hausnummer, Stadt und Postleitzahl dürfen nicht NULL sein).
    In bestimmten Postleitzahlenbereichen liegen (in deinem Fall: Bern mit Postleitzahlen 3000, 3011, 3012, 3013).

In [17]:
## Abfrage: Wähle Gebäude aus, für die eine vollständige Adresse in definierten Postleitzahlenbereichen verfügbar ist

# Erstelle eine SQLAlchemy-Engine zur Verbindung mit der PostgreSQL-Datenbank
engine = create_engine(db_connection_url)

# Define SQL query 
sql = """SELECT
                p.osm_id,                  -- OSM-ID des Objekts (eindeutiger Bezeichner)
                p."addr:street",            -- Straßenname des Gebäudes
                p."addr:housenumber",       -- Hausnummer des Gebäudes
                p."addr:city",              -- Stadt, in der sich das Gebäude befindet
                p."addr:postcode",          -- Postleitzahl des Gebäudes
                p.building,                 -- Typ des Gebäudes (z.B. Wohnhaus, Geschäftsgebäude)
                st_transform(p.way, 4326) AS geom -- Geometrie (Position des Gebäudes) im EPSG:4326-Koordinatensystem
        FROM
                public.planet_osm_polygon AS p  -- Auswahl aus der Tabelle planet_osm_polygon, die Polygone (Flächen) enthält
        WHERE
                p."addr:street" IS NOT NULL    -- Die Straße muss definiert sein
                AND p."addr:housenumber" IS NOT NULL -- Die Hausnummer muss definiert sein
                AND p."addr:city" IS NOT NULL  -- Die Stadt muss definiert sein
                AND p."addr:postcode" IN ('3000', '3011', '3012', '3013') -- Die Postleitzahl muss in Bern sein"""

# Führe die SQL-Abfrage aus und speichere das Ergebnis in einem GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine)

# Schließe die Engine, um die Verbindung zur Datenbank zu beenden
engine.dispose()

# Gib das GeoDataFrame aus, um das Ergebnis der Abfrage anzuzeigen
gdf

# Stellt sicher, dass das GeoDataFrame das richtige Koordinatensystem (EPSG:4326) verwendet
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Berechne die Mittelpunkte (Centroid) der Geometrien, um den Kartenschwerpunkt zu berechnen
centroids = gdf.geometry.centroid
lon = centroids.x.mean()  # Durchschnitt der Längengrade
lat = centroids.y.mean()  # Durchschnitt der Breitengrade

# Initialisiere die Karte, zentriert auf die berechneten Koordinaten (lon, lat) mit einer Zoom-Stufe von 15
m = folium.Map(location=[lat, lon], 
               zoom_start=15,
               tiles='EsriWorldImagery')  # Verwendet den EsriWorldImagery-Kartenstil

# Füge die GeoJSON-Daten (Gebäudegeometrien) zur Karte hinzu
folium.GeoJson(
    gdf,
    name='geojson',
    weight=0.5,  # Linienstärke der Gebäudegrenzen
    fill_color='greenyellow',  # Füllfarbe für die Gebäude
    fillOpacity=0.8,  # Transparenz der Füllung
    popup=folium.GeoJsonPopup(fields=['addr:street', 'addr:housenumber', 'addr:city', 'addr:postcode', 'building'])  # Popup mit Adressdaten
).add_to(m)

# Füge eine Ebenensteuerung zur Karte hinzu
folium.LayerControl().add_to(m)

# Zeige die Karte an
m


## Query: Select coffee stores in Switzerland
    
- Koordinatensystem sicherstellen: Der Code überprüft, ob das GeoDataFrame ein gültiges Koordinatensystem hat. Falls nicht, wird es auf EPSG:4326 gesetzt, ein Standard für geografische Daten (mit Längen- und Breitengraden).
- Kartenmittelpunkt berechnen: Um sicherzustellen, dass die Karte das relevante Gebiet anzeigt, werden die Mittelpunkte der Gebäude berechnet. Der Durchschnitt dieser Mittelpunkte wird als zentraler Punkt verwendet, um die Karte zu zentrieren.
- Karte initialisieren: Die Karte wird mit einem Startzoom von 15 erstellt (detaillierter Zoom). Der Hintergrund der Karte ist der Satellitenkartenstil EsriWorldImagery.
- GeoJSON-Daten hinzufügen: Die geometrischen Daten (Gebäude) aus dem GeoDataFrame werden als GeoJSON auf der Karte dargestellt, mit einer halbtransparenten grün-gelben Füllung und einem Popup, das bei Klick auf ein Gebäude die Adresse und Gebäudetyp anzeigt.
- Layer-Steuerung: Die LayerControl-Funktion fügt der Karte eine Steuerung hinzu, mit der der Benutzer zwischen verschiedenen Ebenen oder Kartenstilen wechseln kann.
- Karte anzeigen: Die Karte wird in einem interaktiven Fenster angezeigt, z.B. in einem Jupyter Notebook.

In [8]:
# Erstellen der SQLAlchemy-Engine zur Verbindung mit der PostgreSQL-Datenbank
# Die Engine wird verwendet, um SQL-Abfragen auszuführen und mit der Datenbank zu kommunizieren
engine = create_engine(db_connection_url)  

# Definieren der SQL-Abfrage
# Diese Abfrage wählt alle Objekte aus der Tabelle 'planet_osm_point', 
# bei denen das Attribut 'shop' auf 'coffee' gesetzt ist (also Geschäfte, die als Kaffeehäuser definiert sind)
# Die Geometrie (Position) dieser Objekte wird in das Koordinatensystem EPSG:4326 (WGS 84) transformiert
sql = """SELECT
            h.osm_id,          -- Eindeutiger Bezeichner des Objekts (OSM-ID)
            h.shop,            -- Typ des Geschäfts (in diesem Fall 'coffee')
            h.name,            -- Name des Kaffees (z.B. Name des Geschäfts)
            ST_Transform(h.way, 4326) AS geom  -- Die Geometrie (Position) des Geschäfts im EPSG:4326-Koordinatensystem
        FROM planet_osm_point h  -- Abfrage der Punktobjekte in der Tabelle 'planet_osm_point'
        WHERE h.shop = 'coffee';  -- Nur Geschäfte auswählen, deren Typ 'coffee' ist"""

# Ausführen der SQL-Abfrage und Speichern des Ergebnisses in einem GeoDataFrame
# GeoDataFrame ist eine spezielle Form eines DataFrames, die räumliche Daten (Geometrien) enthält
gdf = gpd.GeoDataFrame.from_postgis(sql, engine)

# Schließen der Verbindung zur Datenbank
engine.dispose()


In [9]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)  

# Define SQL query
sql = """SELECT
            h.osm_id,
            h.shop,
            h.name,
            ST_Transform(h.way, 4326) AS geom
        FROM planet_osm_point h
        WHERE h.shop = 'coffee';"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine)

# Dispose the engine
engine.dispose()

# Print the GeoDataFrame
gdf


osm_id    shop                                         name  \
0    10275946038  coffee                                 Quinta Coira   
1     9999220377  coffee                                  Presto Café   
2     9935502918  coffee                            The Greek Project   
3     5615258892  coffee                             Pappy John & Cie   
4     4358576994  coffee                                Cafés Trottet   
..           ...     ...                                          ...   
113  11993710081  coffee                                Berger Kaffee   
114   3914484865  coffee  Nurissa Shop / Nespresso Business Solutions   
115  10606177703  coffee                          Kaffee Macher:innen   
116   8909393062  coffee                                    Moccaraba   
117   3322977512  coffee                                       Tchibo   

                         geom  
0     POINT (9.53125 46.8485)  
1    POINT (6.67867 46.52378)  
2    POINT (6.63765 46.51983)  
3    POINT (6.58014 46.53798)  
4    POINT (6.07233 46.22332)  
..                        ...  
113  POINT (7.62597 46.87853)  
114  POINT (7.28529 47.16039)  
115   POINT (7.5891 47.54444)  
116  POINT (7.59199 47.56274)  
117  POINT (7.94814 47.55261)  

[118 rows x 4 columns]

## Show selected features on map

In [10]:
# Stellt sicher, dass das GeoDataFrame das richtige Koordinatensystem (EPSG:4326) verwendet
# EPSG:4326 ist ein gängiges geographisches Koordinatensystem (WGS 84), das Längen- und Breitengrade verwendet
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)  # Wenn das GeoDataFrame kein Koordinatensystem hat, setze es auf EPSG:4326
else:
    pass  # Wenn das Koordinatensystem bereits korrekt ist, tue nichts

# Berechne die Mittelpunkte (Centroid) der Geometrien (z.B. Punkte für Cafés), um den Kartenschwerpunkt zu berechnen
centroids = gdf.geometry.centroid  # Berechnet den Schwerpunkt (Mittelpunkt) jeder Geometrie im GeoDataFrame
lon = centroids.x.mean()  # Berechnet den Durchschnitt der Längengrade (x-Koordinate) für den zentralen Längengrad
lat = centroids.y.mean()  # Berechnet den Durchschnitt der Breitengrade (y-Koordinate) für den zentralen Breitengrad

# Initialisiere die Karte, zentriert auf die berechneten Koordinaten (lon, lat) mit einer Start-Zoom-Stufe von 9
m = folium.Map(location=[lat, lon],  # Legt den Mittelpunkt der Karte auf die berechneten Koordinaten
               zoom_start=9,  # Der Startzoom (9 bedeutet eine moderate Vergrößerung, um die Region zu sehen)
               tiles='EsriWorldTopoMap')  # Verwendet den "EsriWorldTopoMap"-Hintergrundstil (eine topografische Karte)

# Füge die GeoJSON-Daten (Punkt-Geometrien der Cafés) zur Karte hinzu
# Dies ermöglicht es, die Daten (Cafés) auf der Karte zu visualisieren
folium.GeoJson(
    gdf,  # Das GeoDataFrame, das die räumlichen Daten (Geometrien) und Attribute enthält
    name='map',  # Name des Layers auf der Karte
    # Popup-Einstellungen: Diese Felder werden angezeigt, wenn man auf ein Café klickt
    popup=folium.GeoJsonPopup(fields=['name', 'shop'])  # Popups zeigen den Namen des Cafés und den Typ des Shops an
).add_to(m)  # Füge diese Daten zur Karte hinzu

# Füge eine Ebenensteuerung zur Karte hinzu, damit der Benutzer zwischen verschiedenen Ebenen oder Kartenstilen wechseln kann
folium.LayerControl().add_to(m)


In [11]:
# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Calculate the mean longitude and latitude for the map center
centroids = gdf.geometry.centroid
lon = centroids.x.mean()
lat = centroids.y.mean()

# Initialize the map
m = folium.Map(location=[lat, lon], 
               zoom_start=9, 
               tiles='EsriWorldTopoMap')

# Map settings
folium.GeoJson(
    gdf,
    name='map',
    popup=folium.GeoJsonPopup(fields=['name', 'shop'])
).add_to(m)

folium.LayerControl().add_to(m)

# Plot map
m

## Query: Select all supermarkets in a distance of 1000m around the central station in the city of Winterthur.

<span style="color: blue;">Note:</span>

<span style="color: blue;">For each supermarket, the distance to the central station in meters is calculated and stored as new column 'distance_meters'.</span>

<span style="color: blue;">In addition, a popup field was added to the map, allowing users to view detailed information about each selected feature when they click on it.</span>

<span style="color: blue;">The WGS84 (World Geodetic System 1984) coordinates in ST_MakePoint(LON, LAT) were derived from: https://tools.retorte.ch/map.</span>

grosse Zahl ist immer Latitude und die kleine ist Longitude


In [12]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)  

# Define SQL query
sql = """SELECT
            p.osm_id,
            p.shop,
            p.name,
            ST_Distance(
                ST_Transform(p.way, 4326)::geography,
                -- Central station coordinates
                ST_SetSRID(ST_MakePoint(8.72397, 47.50031), 4326)::geography
            ) AS distance_meters,
            ST_TRANSFORM(p.way, 4326) AS geom
        FROM
            planet_osm_point AS p
        WHERE
            p.shop = 'supermarket'
            AND ST_DWithin(
                ST_Transform(p.way, 4326)::geography,
                -- Central station coordinates
                ST_SetSRID(ST_MakePoint(8.72397, 47.50031), 4326)::geography,
                1000
            )
        ORDER BY distance_meters;"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine)

# Dispose the engine
engine.dispose()

# Print the GeoDataFrame
gdf


osm_id         shop                          name  distance_meters  \
0   706203439  supermarket                          Coop       159.883419   
1  4109460421  supermarket                     Asia Shop       162.391281   
2  3831772784  supermarket                        Migros       247.578208   
3  7380954145  supermarket                      Alnatura       256.838011   
4  4095400190  supermarket                          ALDI       274.275393   
5  4125136758  supermarket  Tandoor Indischer Supermarkt       290.212664   
6  4095400136  supermarket                        Denner       316.354037   
7   709022324  supermarket               Claro Weltladen       441.129317   
8  4058248551  supermarket                        Migros       600.117307   
9  3441033104  supermarket                L'Ultimo Bacio       680.202961   

                       geom  
0  POINT (8.72594 47.50085)  
1  POINT (8.72208 47.50101)  
2  POINT (8.72115 47.49916)  
3  POINT (8.72074 47.49958)  
4   POINT (8.72476 47.4979)  
5  POINT (8.72017 47.50073)  
6  POINT (8.72036 47.49886)  
7  POINT (8.72912 47.49842)  
8  POINT (8.73193 47.50012)  
9  POINT (8.73299 47.49999)

# Was anpssen, wenn andere Location oder Feature

#### 1. Geografische Koordinaten (Längengrad und Breitengrad):

Die Koordinaten, die derzeit für den Hauptbahnhof Winterthur verwendet werden, befinden sich in den folgenden Teilen des Codes:

```sql

ST_SetSRID(ST_MakePoint(8.72397, 47.50031), 4326)::geography
```

- Diese Werte repräsentieren den Längengrad (8.72397) und den Breitengrad (47.50031).
- Um eine andere Location (z.B. einen Bahnhof oder einen Punkt in einer anderen Stadt) zu verwenden, musst du diese Werte durch die neuen Koordinaten der gewünschten Location
    ersetzen. Du kannst die Koordinaten von Orten beispielsweise mit Tools wie Google Maps oder speziellen Kartenwerkzeugen wie retorte.ch/map abrufen.

Beispiel: Koordinaten für den Hauptbahnhof Zürich:

- Längengrad: 8.539183
- Breitengrad: 47.378177

Ändere also den entsprechenden Teil der Abfrage zu:

```sql
ST_SetSRID(ST_MakePoint(8.539183, 47.378177), 4326)::geography
```

### 2. Filter für andere Features (z.B. Shop-Typ):

Im aktuellen Code wird nach Supermärkten gefiltert:

```sql
p.shop = 'supermarket'
```

Wenn du nach einem anderen Feature (z.B. Cafés, Restaurants, Bahnhöfe) suchen möchtest, musst du den Filter p.shop = 'supermarket' anpassen.
Beispiele:
- Für Cafés: p.shop = 'cafe'
- Für Restaurants: p.shop = 'restaurant'
- Für Polizeistationen (anstelle von shop, amenity verwenden): p.amenity = 'police'

### 3. Radius der Abfrage:

Im aktuellen Code ist der Radius auf 1000 Meter (1 Kilometer) um den Punkt festgelegt:

```sql
AND ST_DWithin(
    ST_Transform(p.way, 4326)::geography,
    ST_SetSRID(ST_MakePoint(8.72397, 47.50031), 4326)::geography,
    1000
)
```

Um den Radius zu ändern, musst du den Wert 1000 anpassen. Zum Beispiel:
- Für einen Radius von 500 Metern: 500
- Für einen größeren Radius, z.B. 2000 Meter: 2000

## Show selected features on map

In [13]:
# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Calculate the mean longitude and latitude for the map center
centroids = gdf.geometry.centroid
lon = centroids.x.mean()
lat = centroids.y.mean()

# Initialize the map
m = folium.Map(location=[lat, lon], 
               zoom_start=16, 
               tiles='ESRIWorldImagery')

# Map settings
folium.GeoJson(
    gdf,
    name='map',
    popup=folium.GeoJsonPopup(fields=['name', 'distance_meters'])
).add_to(m)

folium.LayerControl().add_to(m)

# Plot map
m

## Query: Select all roads classified as 'motorway' and create a 5000m buffer around these roads.

In [14]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Define SQL query (major roads)
sql = """-- Create buffer around major roads
        SELECT 
            1 as group_id,
            ST_TRANSFORM(ST_UNION(ST_Buffer(p.way::geometry, 5000)), 4326) AS geom
        FROM public.planet_osm_roads AS p
        WHERE
            highway = 'motorway';"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine, geom_col='geom')

# Dispose the engine
engine.dispose()

## Show selected features on map

In [15]:
# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Calculate the mean longitude and latitude for the map center
centroids = gdf.geometry.centroid
lon = centroids.x.mean()
lat = centroids.y.mean()

# Initialize the map
m = folium.Map(location=[lat, lon], 
               zoom_start=9, 
               tiles='EsriWorldTopoMap')

# Map settings
folium.GeoJson(
    gdf,
    name='map'
).add_to(m)

folium.LayerControl().add_to(m)

# Plot map
m

#### Flüsse anstatt Autobahnen

1. Tabelle ändern:
        In OpenStreetMap sind Flüsse in der Regel in der Tabelle planet_osm_line oder planet_osm_polygon gespeichert, da Flüsse entweder als Linien (für Flussverläufe) oder als Polygone (für größere Flussflächen) dargestellt werden.
        Du solltest also die Tabelle von planet_osm_roads auf planet_osm_line ändern.

2. Bedingung für Flüsse:
        Anstelle des Attributs highway = 'motorway', musst du nach Flüssen filtern. Flüsse werden in OpenStreetMap typischerweise durch das Attribut waterway = 'river' definiert.
        Du änderst also die Bedingung zu waterway = 'river'.

3. Puffer anpassen:
        Die Funktion ST_Buffer() wird verwendet, um einen Puffer um geometrische Objekte zu erstellen. Je nach Bedarf kannst du den Pufferwert (in Metern) anpassen, um eine Pufferzone um die Flusslinien zu erstellen. Wenn du keinen Puffer benötigst, kannst du diese Funktion entfernen.

### Code:
```Python
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Define SQL query (for rivers)
sql = """-- Create buffer around rivers
        SELECT 
            1 as group_id,  -- Gruppierung, um alle Flüsse in einer Geometrie zu kombinieren
            ST_TRANSFORM(ST_UNION(ST_Buffer(p.way::geometry, 500)), 4326) AS geom  -- Puffer von 500 Metern um die Flüsse
        FROM public.planet_osm_line AS p  -- Ändere die Tabelle auf 'planet_osm_line', die Linien enthält
        WHERE
            p.waterway = 'river';"""  -- Filter, um nur Flüsse ('river') zu selektieren

# Query the database and store the result in a GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine, geom_col='geom')

# Dispose the engine
engine.dispose()

# Print the GeoDataFrame
gdf
```

#### Code ohne Puffer:
```Python
sql = """SELECT 
            1 as group_id,
            ST_TRANSFORM(ST_UNION(p.way::geometry), 4326) AS geom
        FROM public.planet_osm_line AS p
        WHERE
            p.waterway = 'river';"""

```

### unerer Code

``` Python
# Stellt sicher, dass das GeoDataFrame das richtige Koordinatensystem (EPSG:4326) verwendet
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Berechne die Mittelpunkte (Centroid) der Flüsse, um den Kartenschwerpunkt zu berechnen
centroids = gdf.geometry.centroid  # Berechnet den Mittelpunkt der Geometrien (Flusslinien)
lon = centroids.x.mean()  # Durchschnitt der Längengrade
lat = centroids.y.mean()  # Durchschnitt der Breitengrade

# Initialisiere die Karte, zentriert auf den berechneten Kartenschwerpunkt
m = folium.Map(location=[lat, lon], 
               zoom_start=9,  # Angepasster Zoom-Faktor, um eine bessere Übersicht der Flüsse zu bieten
               tiles='EsriWorldTopoMap')  # Verwendet die Esri-TopoMap-Karte

# Füge die GeoJSON-Daten (Flussgeometrien) zur Karte hinzu
folium.GeoJson(
    gdf,  # Das GeoDataFrame mit den räumlichen Daten (Flüsse)
    name='Flüsse'  # Name des Layers
).add_to(m)

# Füge eine Steuerung hinzu, damit Benutzer zwischen Layern wechseln können (falls mehrere Ebenen vorhanden sind)
folium.LayerControl().add_to(m)

# Zeige die Karte an
m
```


### Jupyter notebook --footer info-- (please always provide this at the end of each notebook)

In [16]:
import os
import platform
import socket
from platform import python_version
from datetime import datetime

print('-----------------------------------')
print(os.name.upper())
print(platform.system(), '|', platform.release())
print('Datetime:', datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
print('Python Version:', python_version())
print('-----------------------------------')

-----------------------------------
POSIX
Linux | 6.5.0-1025-azure
Datetime: 2024-10-06 19:32:03
Python Version: 3.12.1
-----------------------------------
